In [89]:
import os
os.chdir('./..')

In [90]:
import data
import pandas as pd
from tqdm.auto import tqdm
tqdm.pandas()
import numpy as np
from sklearn.preprocessing import MinMaxScaler
from sklearn.utils import shuffle
pd.options.display.max_columns = None
from keras.callbacks import EarlyStopping
from sklearn.model_selection import train_test_split
from keras.utils import to_categorical
from sklearn.utils import class_weight
from sklearn.metrics import classification_report


In [3]:
import keras
from keras import metrics
from keras import Sequential
from keras.layers import Dense, Dropout
from keras import regularizers
from keras.metrics import top_k_categorical_accuracy

In [2]:
a =range(20)

In [3]:
a

range(0, 20)

### create the MRR as a metrics to evaluate the model

In [25]:
def _extract_features(df, submission_mode=False):
    # get the rows where the action is 'clickout item'
    if submission_mode:
        clickout_rows_df = df[(df['action_type'] == 'clickout item') & df['reference'].isnull()]
    else:
        clickout_rows_df = df[df['action_type'] == 'clickout item']

    if len(clickout_rows_df) > 0:

        # features
        features = {
            # impressions features
            'times_impression_appeared': [],
            'time_elapsed_from_last_time_impression_appeared': [],
            'steps_from_last_time_impression_appeared': [],
            'kind_action_reference_appeared': [],
            'impression_position': [],
            'label': [],
            'price': [],
            'price_position': [],
            'delta_position': [],

            # session features
            'session_length': [],
            'session_steps': [],
            'time_from_last_action': [],
            'reference_position_last_action': [],
            'timestamp':[],
            'average_price_clickout':[],

            'index': []}

        clk = clickout_rows_df.tail(1)

        head_index = df.head(1).index

        # considering only the past!
        # mantain of the df only the actions before the last clickout
        df = df.loc[head_index.values[0]:clk.index.values[0] - 1]
        
        if len(df) > 0:
            clickouts = df[df['action_type']=='clickout item']
            if len(clickouts)>0:
                mean_price = 0
                for i,row in clickouts.iterrows():
                    impr = list(map(int, row.impressions.split('|')))
                    prices = list(map(int, row.prices.split('|')))
                    ref = int(row.reference)
                    if ref in impr:
                        pos = impr.index(ref)
                        mean_price += prices[pos]
                mean_price/=len(clickouts)
                if mean_price == 0:
                    mean_price = -1
            else:
                mean_price = -1
                    
            session_length = clk['timestamp'].values[0] - df.head(1)['timestamp'].values[0]
            time_from_last_action = clk['timestamp'].values[0] - df.tail(1)['timestamp'].values[0]
            
            if df.tail(1)['reference'].values[0].isdigit():
                last_ref = int(df.tail(1)['reference'])
            else:
                last_ref = 0
        else:
            session_length = -0.5
            time_from_last_action = -0.5
            last_ref = -0.5
            mean_price = -1
        session_steps = clk['step'].values[0]

        # get the impression
        impr = list(map(int, clk['impressions'].values[0].split('|')))

        if last_ref in impr:
            reference_position_last_action = impr.index(last_ref)
        else:
            reference_position_last_action = -0.5

        prices = list(map(int, clk['prices'].values[0].split('|')))
        sorted_prices = prices.copy()
        sorted_prices.sort()

        references = df['reference'].values

        count = 0
        for i in impr:
            if reference_position_last_action >= 0:
                delta_pos = count - reference_position_last_action
            else:
                delta_pos = count
            indices = np.where(references == str(i))[0]

            features['index'].append(clk.index[0])
            features['impression_position'].append(count + 1)
            features['price'].append(prices[count])
            features['price_position'].append(sorted_prices.index(prices[count]))
            if len(indices) > 0:
                row_reference = df.head(indices[-1] + 1).tail(1)
                features['steps_from_last_time_impression_appeared'].append(len(df) - indices[-1])
                features['time_elapsed_from_last_time_impression_appeared'].append(
                    int(clk['timestamp'].values[0] - row_reference['timestamp'].values[0]))
                features['kind_action_reference_appeared'].append(row_reference['action_type'].values[0])
            else:
                features['steps_from_last_time_impression_appeared'].append(-0.5)
                features['time_elapsed_from_last_time_impression_appeared'].append(-0.5)
                features['kind_action_reference_appeared'].append('no_action')
            features['timestamp'].append(clk['timestamp'].values[0])
            features['times_impression_appeared'].append(len(indices))
            features['delta_position'].append(delta_pos)
            features['session_length'].append(session_length)
            features['session_steps'].append(session_steps)
            features['time_from_last_action'].append(time_from_last_action)
            features['reference_position_last_action'].append(reference_position_last_action)
            features['average_price_clickout'].append(mean_price)
            
            if submission_mode:
                features['label'].append(0)
            else:
                if int(clk['reference'].values[0]) == i:
                    features['label'].append(1)
                else:
                    features['label'].append(0)

            count += 1
        """
        # zero padd the impressions with 0 feature values
        missing_impr_count = 25 - len(impr)
        if missing_impr_count > 0:
            for k in features.keys():
                if k == 'label':
                    features[k].extend(np.zeros(missing_impr_count))
                elif k == 'delta_position':
                    features[k].extend(np.ones(missing_impr_count) * 25)
                else:
                    features[k].extend(np.ones(missing_impr_count) * -1)
        """
        return pd.DataFrame(features)


In [297]:
    def func(x, submission_mode=False):
        
        if submission_mode:
            y = x[(x['action_type'] == 'clickout item')& x['reference'].isnull()]
        else:
            y = x[(x['action_type'] == 'clickout item')]
        # TO-DO: user features! ;)
        
        if len(y) > 0:
            
            clk = y.tail(1)
            head_index = x.head(1).index

            # features
            features = {'label': [], 'times_impression_appeared': [], 'time_elapsed_from_last_time_impression_appeared': [], 'impression_position': [],
                        'steps_from_last_time_impression_appeared': [], 'kind_action_reference_appeared_last_time': [],
                        'price': [], 'price_position': [],
                        'item_id': [], 'other change of sort order session': 0, 'other clickout item session': 0,
                        'other filter selection session': 0, 'other interaction item deals session': 0, 'other interaction item image session': 0,
                        'other interaction item info session': 0, 'other interaction item rating session': 0, 'other search for destination session': 0,
                        'other search for item session': 0, 'other search for poi session': 0, 'session length': 0,
                        'device': '', 'filters_when_clickout': '', 'session_length': 0, 'mean_price':0,
                        'index': 0}

            features['session length'] = len(x)
            features['device'] = clk['device'].values[0]
            features['filters_when_clickout'] = clk['current_filters'].values[0]
            features['session_length'] = abs(
                int(clk['timestamp'].values[0]) - int(x.head(1)['timestamp'].values[0]))

            # considering only the past!
            x = x.loc[head_index.values[0]:clk.index.values[0]-1]
            
            if len(x)>0:
                clickouts = x[x['action_type']=='clickout item']
                if len(clickouts)>0:
                    mean_price = 0
                    for i,row in clickouts.iterrows():
                        impr = list(map(int, row.impressions.split('|')))
                        prices = list(map(int, row.prices.split('|')))
                        ref = int(row.reference)
                        if ref in impr:
                            pos = impr.index(ref)
                            mean_price += prices[pos]
                    mean_price/=len(clickouts)
                    if mean_price == 0:
                        mean_price = -1
                else:
                    mean_price = -1
            else:
                mean_price = -1
            features['mean_price']=mean_price

            impr = clk['impressions'].values[0].split('|')
            prices = list(map(int, clk['prices'].values[0].split('|')))
            sorted_prices = prices.copy()
            sorted_prices.sort()

            references = x['reference'].values
            actions = x['action_type'].values
            not_to_cons_indices = []
    
            features['index'] = clk.index[0]
            count = 0
            for i in impr:
                
                indices = np.where(references == str(i))[0]
                not_to_cons_indices += list(indices)
                features['impression_position'].append(count+1)
                features['price'].append(prices[count])
                features['price_position'].append(
                    sorted_prices.index(prices[count]))
                features['item_id'].append(int(i))
                features['times_impression_appeared'].append(len(indices))
                if len(indices) > 0:
                    row_reference = x.head(indices[-1]+1).tail(1)
                    features['steps_from_last_time_impression_appeared'].append(
                        len(x)-indices[-1])
                    features['time_elapsed_from_last_time_impression_appeared'].append(
                        int(clk['timestamp'].values[0] - row_reference['timestamp'].values[0]))
                    features['kind_action_reference_appeared_last_time'].append(
                        'last_time_impression_appeared_as_' + row_reference['action_type'].values[0])
                else:
                    features['steps_from_last_time_impression_appeared'].append(
                        0)
                    features['time_elapsed_from_last_time_impression_appeared'].append(
                        -1)
                    features['kind_action_reference_appeared_last_time'].append(
                        'last_time_reference_did_not_appeared')

                if clk['reference'].values[0] == i:
                    features['label'].append(1)
                else:
                    features['label'].append(0)

                count += 1

            to_cons_indices = list(
                set(list(range(len(actions)))) - set(not_to_cons_indices))
            for ind in to_cons_indices:
                if ('other ' + actions[ind] + ' session') in features:
                    features['other ' + actions[ind] + ' session'] += 1
            return pd.DataFrame(features)

### Preprocess the data

In [298]:
train_df = data.train_df('small')
test_df = data.test_df('small')

train_features_dataframe = train_df.groupby(['user_id', 'session_id']).progress_apply(func)
test_features_dataframe = test_df.groupby(['user_id', 'session_id']).progress_apply(func, submission_mode=True)

In [299]:
train_features_dataframe

label  times_impression_appeared  \
user_id      session_id                                           
0004IOZI7CKF 0146f7cb014ba 0       0                          0   
                           1       0                          0   
                           2       1                          0   
                           3       0                          0   
                           4       0                          0   
                           5       0                          0   
                           6       0                          0   
                           7       0                          0   
                           8       0                          0   
                           9       0                          0   
                           10      0                          0   
                           11      0                          0   
                           12      0                          0   
                           13      0                          0   
                           14      0                          0   
                           15      0                          0   
                           16      0                          0   
                           17      0                          0   
                           18      0                          0   
                           19      0                          0   
                           20      0                          0   
                           21      0                          0   
                           22      0                          0   
                           23      0                          0   
                           24      0                          0   
0008B0X0HC39 1b703eda68d85 0       1                          0   
000EKQEFMW6S c53fab5092ec2 0       0                          0   
                           1       0                          0   
                           2       0                          0   
                           3       0                          0   
...                              ...                        ...   
ZZYRG6A6KZB7 1d6f80c36b646 0       1                          0   
                           1       0                          0   
                           2       0                          0   
                           3       0                          0   
                           4       0                          0   
                           5       0                          0   
                           6       0                          0   
                           7       0                          0   
                           8       0                          0   
                           9       0                          0   
                           10      0                          0   
                           11      0                          0   
                           12      0                          0   
                           13      0                          0   
                           14      0                          0   
                           15      0                          0   
                           16      0                          0   
                           17      0                          0   
                           18      0                          0   
                           19      0                          0   
                           20      0                          0   
                           21      0                          0   
                           22      0                          0   
                           23      0                          0   
                           24      0                          0   
ZZZ4CA1PZ1VU 5fad2053f6f2e 0       0                          0   
                           1       1                          0   
           

### from the impressions features df create the input and the label

In [347]:
features_col = [1,2,3,4,6,7,8,10,11,12,13,14,15,16,17,18,19,22,23]
features_col2=[1,2,8,10,11,12,13,14,15,16,17,18]
features_col3=[1,2,4,6,7,19,22,23]
features_col4 =[1,2,3,4]
features_col5=[6,7,23]

X_test = test_features_dataframe.iloc[:,features_col5]
    
scaler = MinMaxScaler()

# retrieving target indeces
target_indices_duplicated = test_features_dataframe.iloc[:, -1]
target_indeces = target_indices_duplicated.unique()
#for i in range(0, target_indices_duplicated.shape[0], 25):
#    target_indeces.append(target_indices_duplicated[i])

target_indeces = np.array(target_indeces)

# normalize the values
X_test_norm = scaler.fit_transform(X_test)

/home/edoardo/miniconda3/envs/recsys/lib/python3.7/site-packages/sklearn/preprocessing/data.py:323: DataConversionWarning: Data with input dtype int64, float64 were all converted to float64 by MinMaxScaler.
  return self.partial_fit(X, y)


In [348]:
X_test

price  price_position  mean_price
user_id      session_id                                         
004STL2FQU99 24ab1f448fa9c 0      93               4        60.0
                           1      84               1        60.0
                           2     110              10        60.0
                           3     127              15        60.0
                           4      97               7        60.0
                           5     114              11        60.0
                           6     144              18        60.0
                           7     167              23        60.0
                           8      68               0        60.0
                           9      95               5        60.0
                           10    163              21        60.0
                           11    121              14        60.0
                           12     95               5        60.0
                           13    149              19        60.0
                           14     85               2        60.0
                           15    140              17        60.0
                           16    101               8        60.0
                           17    174              24        60.0
                           18    115              12        60.0
                           19    101               8        60.0
                           20    164              22        60.0
                           21    139              16        60.0
                           22    155              20        60.0
                           23     85               2        60.0
                           24    120              13        60.0
009NB737QBAK 3cd8d3096c1c4 0      11               4        -1.0
                           1       9               1        -1.0
                           2      20              13        -1.0
                           3      10               3        -1.0
                           4      26              17        -1.0
...                              ...             ...         ...
ZZW47LRIK2MI 832a72d96ed61 20     86               0       120.0
                           21     93               1       120.0
                           22    108               6       120.0
                           23    145              21       120.0
                           24    119              10       120.0
ZZWHEYWBUNJB 04690b2bf9697 0     128              14        -1.0
                           1     286              24        -1.0
                           2     112              12        -1.0
                           3      93               8        -1.0
                           4     156              17        -1.0
                           5     152              16        -1.0
                           6     186              20        -1.0
                           7     184              19        -1.0
                           8      96               9        -1.0
                           9     161              18        -1.0
                           10    106              11        -1.0
                           11    193              21        -1.0
                           12    112              12        -1.0
                           13     82               5        -1.0
                           14     68               0        -1.0
                           15    203              22        -1.0
                           16    101              10        -1.0
                           17    212              23        -1.0
                           18     88               7        -1.0
                           19     72               2        -1.0
                           20     80               4        -1.0
                           21     69               1        -1.0
                           22     87               6        -1.0
                           23     72               2        -1.0
 

In [349]:
target_indeces

array([ 68488, 235437, 855519, ..., 333481, 235436,  84553])

In [360]:
features_col = [1,2,3,4,6,7,8,10,11,12,13,14,15,16,17,18,19,22,23]
features_col2=[1,2,8,10,11,12,13,14,15,16,17,18]
features_col3=[1,2,4,6,7,19,22,23]
features_col4 =[1,2,3,4]
features_col5=[6,7,23]


# the 5 column is the label
X,Y = train_features_dataframe.iloc[:,features_col5], train_features_dataframe.iloc[:,0]
scaler = MinMaxScaler()
# normalize the values
X_norm = scaler.fit_transform(X) 
Y_norm = Y.values 

/home/edoardo/miniconda3/envs/recsys/lib/python3.7/site-packages/sklearn/preprocessing/data.py:323: DataConversionWarning: Data with input dtype int64, float64 were all converted to float64 by MinMaxScaler.
  return self.partial_fit(X, y)


In [351]:
class_weights = class_weight.compute_class_weight('balanced',
                                                 np.unique(Y_norm),
                                                 Y_norm)

In [352]:
class_weights_dict = {
    0:class_weights[0],
    1:class_weights[1]
}

In [208]:
class_weights_dict

{0: 0.5229922819788789, 1: 11.373213899762254}

shuffle the sample 25 per 25...

## split the data in TRAIN and TEST

In [361]:
X_train, X_val, Y_train, Y_val = train_test_split(X_norm, Y_norm, test_size = 0.2, shuffle=True)

In [382]:
Y_norm

array([0, 0, 1, ..., 0, 0, 0])

In [391]:
temp =np.concatenate((Y_train,Y_val))
class_weights = class_weight.compute_class_weight('balanced',
                                                 np.unique(temp),
                                                 temp)

In [392]:
class_weights

array([ 0.52299228, 11.3732139 ])

In [390]:
(len(np.concatenate((Y_train,Y_val)))-np.sum(np.concatenate((Y_train,Y_val))))/len(np.concatenate((Y_train,Y_val)))

0.95603705299076

In [380]:
len(np.concatenate((Y_train,Y_val)))

947184

In [381]:
len(Y_train)

757747

In [354]:
def model_creator(num_features_per_impressions):
    model = Sequential()
    model.add(Dense(50, input_dim=num_features_per_impressions, activation='relu'))
    model.add(Dropout(rate=0.1))
    model.add(Dense(40, activation='relu'))
    model.add(Dropout(rate=0.1))
    model.add(Dense(30, activation='relu'))
    model.add(Dropout(rate=0.1))
    model.add(Dense(20, activation='relu'))
    model.add(Dense(1, activation='sigmoid'))
    
    # compile the model
    model.compile(loss='binary_crossentropy', optimizer='adam', metrics=['accuracy'])
    return model

In [308]:
model_1 = model_creator(num_features_per_impressions=len(features_col3))

In [223]:
model_2 = model_creator(num_features_per_impressions=len(features_col4))

In [286]:
model_3 = model_creator(num_features_per_impressions=len(features_col2))

In [330]:
model= model_creator(num_features_per_impressions=len(features_col))

In [355]:
model_4 = model_creator(num_features_per_impressions=len(features_col5))

In [363]:
callback = EarlyStopping(monitor='val_loss', min_delta=0, patience=5, verbose=0, mode='auto', baseline=None, restore_best_weights=True)
model_4.fit(X_train, Y_train, validation_data=(X_val, Y_val), epochs=1, class_weight=class_weights_dict, batch_size=128)#, callbacks=[callback])

Train on 757747 samples, validate on 189437 samples
Epoch 1/1
757747/757747 [==============================] - 13s 17us/step - loss: 0.6756 - acc: 0.7181 - val_loss: 0.6831 - val_acc: 0.7622


In [314]:
predictions_1 = model_1.predict(X_test_norm)

In [225]:
predictions_2 = model_2.predict(X_test_norm)

In [288]:
predictions_3 = model_3.predict(X_test_norm)

In [335]:
predictions_4 = model.predict(X_test_norm)

In [366]:
predictions_5 = model_4.predict(X_test_norm)

In [374]:
predictions=predictions_1*1+predictions_2*1+predictions_3*0+predictions_4*0+predictions_5*0.25

In [124]:
Y_val[25:50]

array([0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0])

In [375]:
final_predictions = []

count = 0
accumulator=0
for index in tqdm(target_indeces):
    impr = list(map(int, data.full_df().loc[index]['impressions'].split('|')))
    pred = predictions[accumulator:accumulator+len(impr)]
    print(pred, index)
    accumulator+=len(impr)
    couples = list(zip(pred, impr))
    couples.sort(key=lambda x: x[0], reverse=True)
    _, sorted_impr = zip(*couples)
    final_predictions.append((index, list(sorted_impr)))
    count += 1

[[1.4460943 ]
 [1.2680544 ]
 [0.9700233 ]
 [0.9201363 ]
 [0.97671664]
 [1.7261738 ]
 [0.84107   ]
 [0.7975073 ]
 [1.0709846 ]
 [0.83639187]
 [0.6921251 ]
 [0.68095464]
 [0.76132375]
 [0.6390758 ]
 [0.8303442 ]
 [0.6247594 ]
 [0.67286724]
 [0.60069764]
 [0.6154607 ]
 [0.64861405]
 [0.5749558 ]
 [0.57827914]
 [0.5627486 ]
 [0.7576155 ]
 [0.5632399 ]] 68488
[[1.5232421 ]
 [1.3399028 ]
 [1.0290917 ]
 [1.1397078 ]
 [0.9990217 ]
 [0.9756869 ]
 [0.99487054]
 [1.1209842 ]
 [0.8543229 ]
 [0.8813154 ]
 [0.7953182 ]
 [0.7689778 ]
 [0.7471013 ]
 [0.7377915 ]
 [0.82492214]
 [0.7240225 ]
 [0.76785845]
 [0.7009548 ]
 [0.7756293 ]
 [0.6862097 ]
 [0.67910266]
 [0.66959023]
 [1.038243  ]] 235437
[[1.7255752 ]
 [1.9763678 ]
 [1.7186289 ]
 [0.90396744]
 [0.89512026]
 [0.87706685]
 [0.96078444]
 [0.79408073]
 [0.81256515]
 [0.7483783 ]
 [0.78805035]
 [0.8087622 ]
 [0.67980915]
 [0.62982565]
 [0.62537456]
 [0.63119954]
 [0.6901515 ]
 [0.65047187]
 [0.5969501 ]
 [0.5929259 ]
 [0.62645495]
 [0.6797353 ]
 [0.5

 [0.6535473 ]] 948772
[[1.395716  ]
 [1.2571371 ]
 [0.99503815]
 [0.9756716 ]
 [1.0071273 ]
 [0.94496495]
 [0.9057195 ]
 [0.8647894 ]
 [0.8498333 ]
 [0.7902347 ]
 [0.7594393 ]
 [0.7337549 ]
 [0.73202264]
 [0.70126826]
 [1.1128258 ]
 [0.7823227 ]
 [0.6791776 ]
 [0.7371932 ]
 [0.6612755 ]
 [0.95211995]
 [0.69804615]
 [0.635778  ]
 [0.9289861 ]
 [0.7637268 ]
 [0.7565059 ]] 317915
[[1.3639486 ]
 [1.0472618 ]
 [1.0719866 ]
 [0.93727136]
 [0.9337718 ]
 [0.91012836]
 [0.86302197]
 [0.82559305]
 [0.89603335]
 [0.8650405 ]
 [0.7186351 ]
 [0.70315397]
 [0.6918906 ]
 [0.7008594 ]
 [0.6647966 ]
 [0.78601056]
 [0.7515835 ]
 [0.74352413]
 [0.8072201 ]
 [1.9127166 ]
 [0.8921905 ]] 870328
[[1.5849653 ]
 [1.1217525 ]
 [1.1341679 ]
 [1.0817811 ]
 [1.0001907 ]
 [0.9974279 ]
 [0.9371694 ]
 [1.0724664 ]
 [0.8568302 ]
 [0.8331229 ]
 [0.7971929 ]
 [0.7701778 ]
 [0.74850667]
 [0.7374825 ]
 [0.7277451 ]
 [0.7584927 ]
 [0.7101177 ]
 [0.81877375]
 [0.6948707 ]
 [0.68536913]
 [1.067873  ]
 [0.7608841 ]
 [0.917417

[[1.3840368 ]
 [1.0328069 ]
 [0.9148293 ]
 [0.9689155 ]
 [0.9027648 ]
 [0.91487545]
 [0.88515174]
 [0.896795  ]
 [0.73343337]
 [0.7464161 ]
 [0.77864254]
 [0.69991636]
 [0.80830604]
 [0.6231797 ]
 [0.608752  ]
 [0.6013415 ]
 [0.6081652 ]
 [0.61033404]
 [0.7070034 ]
 [0.7210028 ]
 [0.5710589 ]
 [0.7179612 ]
 [0.55097574]
 [0.6903855 ]
 [0.5380608 ]] 789406
[[2.0548267 ]
 [1.1979634 ]
 [1.019323  ]
 [1.0017269 ]
 [1.384537  ]
 [0.96575576]
 [0.9505638 ]
 [1.2846893 ]
 [0.84210885]
 [0.918794  ]
 [0.7845082 ]
 [0.9336876 ]
 [0.73730874]
 [0.7250972 ]
 [0.80731976]
 [0.8836063 ]
 [0.72355175]
 [0.71549237]
 [0.681591  ]
 [0.76520836]
 [0.66730124]
 [0.6592008 ]
 [0.6519905 ]
 [0.6436572 ]
 [0.63759923]] 789409
[[1.8010901 ]
 [1.1185306 ]
 [1.1078289 ]
 [1.1159548 ]
 [1.0237788 ]
 [1.1469102 ]
 [0.9394159 ]
 [0.9926067 ]
 [0.85464615]
 [0.8245405 ]
 [0.8063451 ]
 [0.8871386 ]
 [0.7527749 ]
 [0.782681  ]
 [0.728551  ]
 [0.85895926]
 [0.9706133 ]] 398419
[[2.0847397]
 [1.5013316]
 [1.1759151]

 [0.6870131 ]] 870863
[[1.7911146]] 949350
[[1.4140966 ]
 [1.1211797 ]
 [1.0333031 ]
 [1.0133685 ]
 [1.0012372 ]
 [1.0918175 ]
 [0.9379829 ]
 [0.9010808 ]
 [0.9575432 ]
 [1.2032577 ]
 [0.79336953]
 [0.8073672 ]
 [0.88608265]
 [0.73719394]
 [0.73090607]
 [0.7281194 ]
 [0.7099653 ]
 [0.70498854]
 [0.86186224]
 [0.68553644]
 [0.71647805]
 [0.7599812 ]
 [0.75231326]
 [0.8969142 ]
 [0.6484033 ]] 856638
[[1.363066  ]
 [1.1148145 ]
 [1.29805   ]
 [0.9601034 ]
 [0.94887817]
 [1.0021366 ]
 [0.8881836 ]
 [0.880633  ]
 [0.9617452 ]
 [0.7715038 ]
 [0.9335121 ]
 [0.71794546]
 [0.82791865]
 [0.7051996 ]
 [0.6762322 ]
 [0.6706356 ]
 [0.73634934]
 [1.0957327 ]
 [0.7417849 ]
 [0.6456505 ]
 [0.6306084 ]
 [0.6214524 ]
 [0.61141866]
 [0.8241216 ]
 [0.6030107 ]] 481010
[[1.4283407 ]
 [1.1186535 ]
 [1.0466615 ]
 [1.0122392 ]
 [1.2257305 ]
 [1.0877198 ]
 [1.3148326 ]
 [1.0115157 ]
 [0.8707083 ]
 [0.9353895 ]
 [0.9542223 ]
 [0.76868033]
 [0.7646473 ]
 [0.8972621 ]
 [0.72687054]
 [0.73499006]
 [0.7262584 ]
 [0

 [2.029529  ]] 871024
[[2.0586488 ]
 [1.1354213 ]
 [1.0252435 ]
 [1.003672  ]
 [0.9940865 ]
 [0.979561  ]
 [0.93221706]
 [0.89524126]
 [0.9525987 ]
 [0.81729954]
 [0.892091  ]
 [0.93190455]
 [0.74128306]
 [0.8487029 ]
 [0.7249121 ]
 [0.7148666 ]
 [0.84357154]
 [1.0841892 ]
 [0.6907415 ]
 [0.9224623 ]
 [0.7072043 ]
 [0.66383266]
 [0.720016  ]
 [0.6480236 ]
 [0.6410625 ]] 936461
[[1.7747636 ]
 [1.3157916 ]
 [1.1841599 ]
 [2.034946  ]
 [1.0753564 ]
 [1.0214427 ]
 [0.9616263 ]
 [0.9065224 ]
 [0.84570724]
 [0.7992197 ]
 [0.75559944]
 [0.724307  ]
 [0.703883  ]
 [0.684094  ]
 [0.67270845]
 [0.6635819 ]
 [0.6543799 ]
 [0.647482  ]
 [0.64055526]
 [0.6336768 ]
 [0.62709606]
 [0.6194532 ]
 [0.61178523]
 [0.6077862 ]
 [0.6017027 ]] 949514
[[1.4436724 ]
 [1.1363038 ]
 [1.0127124 ]
 [0.9877182 ]
 [0.978129  ]
 [1.0380954 ]
 [1.9652257 ]
 [0.878384  ]
 [0.8375515 ]
 [0.80339074]
 [0.77264047]
 [0.7487467 ]
 [0.73174214]
 [0.71419454]
 [0.7456602 ]
 [0.9397317 ]
 [0.931     ]
 [0.67948437]
 [0.672298

...

[[1.3310198 ]
 [1.0260222 ]
 [0.94613516]
 [1.0521183 ]
 [0.9045599 ]
 [0.9760676 ]
 [1.0292386 ]
 [0.8121266 ]
 [0.87413365]
 [0.76301247]
 [0.6990988 ]
 [0.69787645]
 [0.6537719 ]
 [0.6429218 ]
 [0.67966026]
 [0.70108056]
 [0.6321035 ]
 [0.608314  ]
 [0.65984213]
 [0.59178025]
 [1.0059655 ]
 [0.8488149 ]
 [0.56816465]
 [0.5647311 ]
 [0.7891538 ]] 161726
[[1.4133765 ]
 [1.1212919 ]
 [1.0677515 ]
 [1.1784898 ]
 [1.1154609 ]
 [1.0652623 ]
 [0.945691  ]
 [1.0372769 ]
 [0.875044  ]
 [1.2093077 ]
 [0.79345316]
 [0.8848431 ]
 [0.7496832 ]
 [0.82645696]
 [0.7276957 ]
 [0.96771276]] 161727
[[1.7761798]
 [1.848303 ]
 [1.4006453]
 [1.1664448]
 [1.1075197]
 [1.050286 ]
 [1.1503077]
 [1.0558535]] 567859
[[1.4773364]
 [1.8548149]
 [1.1111472]
 [1.0789868]
 [1.0754472]] 801247
[[1.3944682]
 [2.0872679]] 645980
[[1.6625493 ]
 [1.8475723 ]
 [1.720342  ]
 [1.0603526 ]
 [1.0273694 ]
 [0.9853187 ]
 [0.9284882 ]
 [0.87410545]
 [0.81504375]
 [0.7709726 ]] 957705
[[1.3505116 ]
 [1.0230104 ]
 [0.95958155]
 

 [0.6010519 ]] 82388
[[2.03124   ]
 [1.2562532 ]
 [1.2836703 ]
 [1.0056102 ]
 [0.99278045]
 [0.969988  ]
 [0.93194026]
 [1.013442  ]
 [0.8475091 ]
 [0.9079402 ]
 [0.8110273 ]
 [0.7658077 ]
 [0.8098368 ]
 [1.1261413 ]
 [0.73221964]
 [0.7157264 ]
 [0.70316035]
 [0.8703788 ]
 [0.68663174]
 [0.74719465]
 [0.6718562 ]
 [0.66277593]
 [0.6570704 ]
 [0.64873433]
 [0.7472626 ]] 410925
[[1.4130539 ]
 [1.1194733 ]
 [1.0326364 ]
 [1.029723  ]
 [0.9998711 ]
 [0.97572726]
 [0.9385567 ]
 [0.98630524]
 [0.85576934]
 [0.8262987 ]
 [0.89441   ]
 [0.8347292 ]
 [0.75022584]
 [0.7369947 ]
 [0.7937745 ]
 [0.7269174 ]
 [0.8735377 ]
 [0.70116496]
 [0.930701  ]
 [0.6849711 ]
 [0.8110941 ]
 [0.6695052 ]
 [0.66332465]
 [0.7882998 ]
 [1.0283442 ]] 492528
[[1.7823634 ]
 [1.0623931 ]
 [0.98399055]
 [0.9960249 ]
 [1.221946  ]
 [0.9221899 ]
 [0.8823969 ]
 [0.8494353 ]
 [0.8553641 ]
 [0.767926  ]
 [0.84489   ]
 [0.7163289 ]
 [0.7811007 ]
 [0.84940964]
 [0.67576545]
 [0.6653818 ]
 [0.6815684 ]
 [0.6527568 ]
 [0.6426232

 [0.66684777]] 958228
[[1.5587116 ]
 [1.07039   ]
 [0.9412181 ]
 [0.88743997]
 [0.87167984]
 [0.8585495 ]
 [0.805755  ]
 [0.86228716]
 [0.7249492 ]
 [0.68866515]
 [0.7458304 ]
 [0.76678765]
 [0.7002772 ]
 [1.676765  ]
 [0.6159264 ]
 [0.5857441 ]
 [0.7403377 ]
 [0.62290007]
 [1.7780297 ]
 [0.5793948 ]
 [0.8088037 ]
 [0.7609354 ]
 [2.0774524 ]
 [0.6339834 ]
 [0.8165997 ]] 249319
[[1.3570986 ]
 [1.0630313 ]
 [1.0974915 ]
 [0.9568375 ]
 [0.95036143]
 [1.1386797 ]
 [0.93941784]
 [0.8524299 ]
 [0.946836  ]
 [2.0425463 ]
 [0.8124106 ]
 [1.0016949 ]
 [0.7372892 ]
 [0.6809852 ]
 [1.104397  ]
 [0.67249656]
 [0.6546529 ]
 [0.645944  ]
 [0.6415049 ]
 [0.63572204]
 [0.666824  ]
 [0.62441456]
 [0.62419546]
 [0.7880248 ]
 [0.68425465]] 162890
[[1.41334   ]
 [1.1201504 ]
 [1.0301137 ]
 [1.0280278 ]
 [1.0003334 ]
 [0.97610354]
 [1.000112  ]
 [0.90004605]
 [0.9402746 ]
 [0.82406265]
 [0.7965586 ]
 [0.77078074]
 [0.7471665 ]
 [0.7369878 ]
 [0.7268288 ]
 [0.7818317 ]
 [0.94118917]
 [0.8337164 ]
 [0.692907

 [0.6337809 ]] 554892
[[1.2565885 ]
 [1.811748  ]
 [1.6014981 ]
 [1.6663582 ]
 [0.88103414]
 [1.9582047 ]
 [0.77760416]
 [0.80775994]
 [0.7840853 ]
 [0.6706338 ]
 [0.6441593 ]
 [0.8460069 ]
 [0.6046085 ]
 [0.76637614]
 [0.75725245]
 [0.7081442 ]
 [0.5737064 ]
 [0.7537986 ]
 [0.5362138 ]
 [0.6153822 ]
 [0.80106115]
 [0.5518843 ]
 [0.5510116 ]
 [0.5084572 ]
 [0.5177448 ]] 724708
[[1.5296615 ]
 [1.1208692 ]
 [1.0302525 ]
 [1.0141037 ]
 [1.0009696 ]
 [1.0191077 ]
 [0.9391384 ]
 [0.91082704]
 [1.1100852 ]
 [0.82549596]
 [0.96785426]
 [0.76968724]
 [0.74992776]
 [0.7375006 ]
 [0.7274057 ]
 [0.7938194 ]
 [0.7101157 ]
 [0.7025412 ]
 [0.8677267 ]
 [0.68698925]
 [0.6806474 ]
 [1.0583445 ]
 [0.70593333]
 [0.76007   ]
 [0.740471  ]] 250246
[[1.4156351 ]
 [1.2936815 ]
 [1.0307748 ]
 [1.0507405 ]
 [1.1167302 ]
 [1.1165885 ]
 [0.9364992 ]
 [0.9718548 ]
 [0.8576964 ]
 [0.8256855 ]
 [0.8981269 ]
 [0.77145517]
 [0.8393378 ]
 [0.737971  ]
 [0.7285757 ]
 [0.7197208 ]
 [0.71038616]
 [0.72393024]
 [0.961857

 [0.56919897]] 493489
[[1.0479109 ]
 [1.1828363 ]
 [1.0024431 ]
 [0.98221445]
 [0.90246207]
 [0.82431877]
 [0.7874006 ]
 [0.83634824]
 [0.7222382 ]
 [0.7070558 ]
 [1.9026164 ]
 [1.1884588 ]
 [0.6069999 ]
 [0.73922944]
 [0.64516705]
 [0.66611284]
 [0.60649526]
 [0.56665105]
 [0.68109125]
 [0.6128013 ]
 [0.5551839 ]
 [0.6875651 ]
 [0.5591082 ]
 [0.51074505]
 [0.5007204 ]] 569229
[[1.9884437 ]
 [1.1151892 ]
 [1.0215472 ]
 [1.1134924 ]
 [1.1162362 ]
 [0.96586543]
 [0.97052664]
 [1.0453714 ]
 [0.94284   ]
 [0.81221545]
 [0.9720078 ]
 [0.75959295]
 [0.7379138 ]
 [1.1358556 ]
 [1.1267319 ]
 [0.7088963 ]
 [0.70041656]
 [0.69112337]
 [0.6852363 ]
 [0.6773165 ]
 [0.7663139 ]
 [0.677324  ]
 [0.65242636]
 [0.688644  ]
 [0.637372  ]] 235285
[[1.8071088 ]
 [1.1447675 ]
 [1.0443292 ]
 [0.9929316 ]
 [0.982448  ]
 [1.0262662 ]
 [0.92124707]
 [0.90008515]
 [1.0273067 ]
 [0.9356127 ]
 [0.77896285]
 [0.7567992 ]
 [0.73199046]
 [0.7201154 ]
 [0.71239924]
 [0.7021453 ]
 [0.6937704 ]
 [0.6869438 ]
 [0.789953

In [369]:
final_predictions

[(68488,
  [106474,
   54776,
   99642,
   1151715,
   1583829,
   18286,
   923943,
   117240,
   54739,
   2562011,
   54640,
   1622253,
   99643,
   3849372,
   54662,
   326461,
   54684,
   10246940,
   15143,
   54685,
   54679,
   1184940,
   54715,
   6003096,
   54627]),
 (235437,
  [9719480,
   6058118,
   7048680,
   4541880,
   1263989,
   4519774,
   6060318,
   4519794,
   6352470,
   4683578,
   4525414,
   7053768,
   4590620,
   6059016,
   1342692,
   4943278,
   9700896,
   773003,
   4367388,
   1041762,
   9145838,
   4482020,
   9426686]),
 (855519,
  [33056,
   100625,
   42249,
   5472226,
   153611,
   33139,
   42051,
   2831138,
   100615,
   1048522,
   927233,
   9030278,
   33132,
   106758,
   4354786,
   1969335,
   1387985,
   3820210,
   9283434,
   42250,
   6679258,
   42106,
   971405,
   6465202,
   14785]),
 (397820,
  [3949472,
   2894164,
   2090078,
   1393488,
   1526483,
   4400710,
   1158295,
   7934200,
   2756584,
   1264210,
   2038739,

In [376]:
target_indices, recs = zip(*final_predictions)
target_indices = list(target_indices)
correct_clickouts = data.full_df().loc[target_indices].reference.values
len_rec = len(recs)

RR = 0
print("Calculating MRR (hoping for a 0.99)")
for i in tqdm(range(len_rec)):
    correct_clickout = int(correct_clickouts[i])
    print(correct_clickout)
    if correct_clickout in final_predictions[i][1]:
        rank_pos = recs[i].index(correct_clickout) + 1
        print(rank_pos)
        if rank_pos <= 25:
            RR += 1 / rank_pos

MRR = RR / len_rec
print(f'MRR: {MRR}')

Calculating MRR (hoping for a 0.99)


1622253
1
6058118
2
42106
5
2039559
21
161614
25
918913
2
8561
12
1387124
1
6980716
9
7933124
13
163254
3
27898
1
3467506
8
18952
1
95371
1
3050674
24
3535082
1
6700870
12
1363808
1
8778552
2
5101386
8
1544579
10
59167
1
1052058
1
32646
8
39405
24
8742268
1
4039826
1
971431
1
5795860
1
2352764
2
2025287
9
1750551
6
1447919
1
9162564
6
12486
2
2140876
1
7917790
5
41892
13
40847
1
448576
1
68473
1
893927
1
1258232
1
439656
5
34369
4
5739276
10
129720
3
1043386
5
348941
1
103574
3
8725
1
41219
1
795656
3
2088146
1
6401436
13
106209
1
486686
1
2715474
1
7194496
1
9634216
6
2641198
3
123259
1
8578
13
116290
3
107312
1
1880135
1
8439876
6
2718378
1
40576
1
1733937
6
7284322
1
1120701
4
343661
1
4487886
1
1739373
1
2460840
1
44351
3
41794
1
10144114
3
4529648
19
4776894
1
53072
1
34555
1
5487888
5
3480558
1
9738828
2
1421451
1
504971
19
990315
1
2208824
1
1475789
2
1652507
1
2269838
1
5050054
3
7359276
1
123666
1
2395686
1
103562
1
5772826
1
2326602
7
2454139
2
137995
1
54581
1
1136385
1
2032

198171
2
1046730
1
3941140
2
103201
14
1309782
2
5791
1
5174478
4
7070864
4
2201134
1
2753326
1
1283086
1
9606310
1
1027020
1
2372368
13
1328267
1
2021869
1
2092816
4
3053490
1
503201
1
152257
1
5005660
6
8551
1
1366664
1
9176136
24
4493756
4
477866
13
520066
4
155753
1
1510073
1
5212864
17
1962145
1
2658708
1
76862
1
3842190
5
37515
4
100295
1
6982518
2
2027073
1
326856
1
3218164
1
4595104
21
8767676
1
54767
1
1625015
2
52979
1
6500
1
385381
3
894191
22
5948820
1
48553
2
795816
1
4556576
1
2884070
3
705071
1
1362220
24
58627
2
148956
17
34430
1
109324
1
1739057
6
2676406
9
3053490
3
8231042
1
8767436
1
97610
1
3971372
3
2360798
1
1166962
1
1335107
1
113401
1
12509
1
91429
1
196441
1
49813
1
163953
1
12743
6
4058648
3
9252816
6
1499989
1
1993587
1
377316
1
2749083
2
3928982
2
1825989
2
82096
19
5945462
2
50106
2
1954459
1
120773
1
695501
1
6435712
1
5169
1
6989
12
3148716
5
429586
2
1892941
1
494496
2
1585657
2
7952142
2
7987824
6
2498278
21
853456
1
14846
8
172377
1
6954018
4
31060
1


2
2765261
1
960121
6
7819
13
689976
5
5724480
1
105444
15
1710817
3
101044
1
2705912
1
1944295
21
5163166
6
151988
1
2012891
14
1955813
5
1127559
2
9378828
1
104808
1
4110236
1
7067650
1
4592920
1
4929602
1
99059
5
750276
5
1969155
1
3213905
1
8489424
15
9474072
3
2839783
1
5967314
1
9337432
6
1894675
1
80914
1
43366
12
15439
1
3183200
1
7889182
4
2076636
7
2497702
13
34448
1
9315914
13
1108993
5
42184
1
35576
1
2605622
2
2454120
9
3236410
7
1650773
5
3747880
1
1668387
1
4341234
1
2528328
1
110652
1
20524
1
1890975
2
2041505
2
47133
9
3148916
2
34337
1
126686
1
2837732
1
5250
8
1310884
1
4586960
2
3989688
9
2265482
1
6823896
8
138087
1
29801
1
763998
15
5818196
2
2402619
1
10636344
25
125340
1
1393443
2
2848906
5
104951
5
3973646
1
167652
2
9600892
1
2505715
1
67806
9
93914
18
5860828
1
1258418
23
42494
6
3201242
1
496141
1
2238570
3
105009
1
3373564
3
18197
21
427596
5
4498786
1
1496365
1
6177052
2
2759893
1
57173
21
2124540
1
37467
1
79612
1
2705840
1
2062876
5
2651858
6
2395686
1
81

12
5560
1
8256092
1
6454992
17
2828701
1
3826192
2
4087020
1
9011526
18
128811
1
10656652
13
2378829
1
2273550
1
5645466
2
885117
1
395456
10
3141536
2
39660
1
1936313
2
3053490
1
6437298
3
111060
1
8589
1
10594196
11
7306718
1
2296554
1
1299956
16
103484
3
8457514
10
7986384
12
136945
2
148508
5
5850586
4
3958078
1
1788539
2
917627
1
1105666
1
2831176
2
7191196
4
8933
1
192876
5
4050070
1
913095
7
5825024
1
1295702
1
163813
1
8205184
1
101902
1
948165
5
42693
1
2730948
1
8925
2
84387
1
364506
2
2627976
5
3501452
2
51863
16
9516298
13
7069926
2
6475414
1
1961709
1
1715471
1
320281
1
2624378
1
2745276
1
6367078
15
2651122
1
436416
21
1088680
23
5521314
1
3854314
1
151785
1
2580846
1
9406682
4
91577
1
2671212
15
52419
1
7866024
14
34440
12
3811810
1
4763850
1
6741038
4
5433616
8
1353892
3
18755
1
475701
1
1811137
1
238426
3
5036544
3
2431278
2
6300600
10
39962
1
34350
2
2861540
1
351471
6
2950734
1
6986
6
3132670
1
503251
1
8577
1
1267405
1
3500952
25
4342558
1
6336686
1
2788164
2
477766

53165
2
2320838
1
1535593
1
8561
1
667221
1
2384685
4
7176
1
19031
16
8848
1
1332274
1
42543
1
104329
4
2956636
1
8266870
10
134921
1
8797196
1
883697
2
2853110
1
4973280
2
56863
1
48154
1
5816996
1
983721
1
8744
1
1490105
1
10120312
12
15524
1
22536
1
69140
1
3815310
1
3930664
3
147522
3
5494918
2
105825
1
127736
1
3971414
1
19128
1
4664048
3
8482514
12
739626
5
5202
1
5917874
1
1059616
1
8830
1
4135528
11
44682
3
2606168
1
82050
11
13507
1
90608
8
470546
1
339951
4
1978807
3
674221
3
15940
10
8755832
1
238226
1
17108
7
1386560
2
823791
2
1239910
7
1321554
2
1184406
4
5994310
3
152984
1
5887030
11
8174858
1
49356
16
693191
1
3967512
1
531976
1
5823814
6
3880624
4
104607
1
792741
1
9168
1
8002404
1
134990
10
164524
2
1015377
7
8796
2
13815
1
8203
1
6295882
4
29801
1
9252706
1
4844958
1
2952802
10
2627982
1
54551
19
7213246
3
6549266
4
5056696
1
4507458
4
100277
5
128297
6
337016
2
368336
1
59180
1
1668375
2
3820210
2
2709976
1
9377514
1
321771
7
6129038
1
1864631
8
571196
1
48078
1
104

96782
1
3048950
2
674276
1
2645772
10
5203886
18
3093802
1
342646
20
5639328
6
2815888
8
1411767
3
99000
1
41193
1
3161938
1
2627976
5
104549
5
107343
6
964265
1
94962
11
7412630
23
52929
1
2502874
2
43620
20
1322096
2
57400
7
15937
11
3834988
2
2848280
1
44146
10
911177
5
5125308
1
104832
1
1099570
8
11042346
1
1976493
1
1022553
1
2862270
1
1329225
7
849261
1
3766912
1
1561165
1
46986
3
82013
1
10217156
1
9536650
10
71746
1
3741160
5
8498
7
55032
1
1638983
1
2206338
1
2417158
1
30956
7
137190
1
1291948
7
9782
1
10156146
23
9022916
10
96670
1
7991052
8
6806560
7
151374
2
3433838
1
9489940
2
1945615
1
3506474
1
2662081
1
9782948
2
151111
12
1023812
1
1217576
1
1811137
1
1894529
4
4744122
9
3810620
3
3835270
1
7390
1
138306
1
32580
1
8809
9
9004316
2
35268
2
104892
12
85470
1
9915560
1
396031
1
231886
1
1380962
1
834526
3
6662954
1
96624
1
3822132
1
10052734
1
7166984
10
974425
1
2292090
1
5523294
6
80416
8
3895722
15
112525
1
6916464
12
1853695
1
73649
10
3950324
7
65284
1
6123386
1
271

1
2884070
3
2380875
11
8978352
1
40899
2
1811137
3
2027891
1
4877026
7
1336377
10
3852052
1
5897
4
923037
2
82204
1
6509
2
54798
9
2553608
1
15113
5
1993405
1
10197810
22
2272294
18
3216982
1
46187
1
81599
1
377716
1
104594
1
6995484
25
2631430
15
16178
2
1269936
1
2267426
1
103495
1
904963
2
2106348
1
3219896
6
1799509
5
95684
1
7680058
4
2600064
2
6953024
1
46732
1
3249168
1
3816106
4
3477578
3
10067460
2
947851
18
494166
5
104315
1
10460448
1
929443
1
42999
1
101767
4
14030
1
17609
1
9416724
1
1031624
1
60252
1
4553860
10
2120928
1
1798951
6
980609
1
1506341
2
1072440
1
2326194
1
2367456
1
2031907
2
3939568
6
1020529
19
13772
2
1771039
9
40719
9
8796
1
2629161
2
9970078
3
2128292
13
40164
1
63302
1
1109480
1
569561
4
1472297
4
1220378
1
2839244
6
12589
1
6737802
1
1656747
3
9767132
1
346846
2
8199
20
43662
3
5060372
3
3487018
1
1386952
6
693591
1
1044320
1
13994
1
12565
1
102067
1
138851
1
359751
2
29801
1
9448
1
1472445
4
3066640
1
97610
7
34504
1
52951
1
67701
1
7797506
1
1711421


1
99184
2
1707113
1
1153426
9
1211182
4
4087590
1
948643
12
1774423
1
6538036
1
1042004
1
741721
5
1527953
1
630411
4
5658634
1
5917060
10
7384618
1
2826362
1
1016951
3
64107
1
122308
4
1358678
1
12810
16
4779552
1
88448
1
4821216
3
2213014
1
348421
2
2033329
6
948643
1
8788590
1
1301669
16
2686794
6
7126
6
729516
1
93625
10
2819060
1
2830022
1
3094482
1
3101452
1
8902854
3
107368
4
55814
22
103455
12
4890910
1
2349076
2
3980460
1
1065406
1
153868
13
64558
14
9661
1
MRR: 0.6443404826625038


In [101]:
for i in range(10000):    
    print(f'pred:{preds_prob[i]}, true:{Y_test[i]}')

pred:[0.16494495], true:0.0
pred:[0.09967062], true:0.0
pred:[0.27539343], true:0.0
pred:[0.12343735], true:0.0
pred:[0.09777829], true:0.0
pred:[0.09348044], true:0.0
pred:[0.07606065], true:0.0
pred:[0.06185529], true:0.0
pred:[0.15322018], true:0.0
pred:[0.09337786], true:0.0
pred:[0.22308332], true:0.0
pred:[0.13207361], true:0.0
pred:[0.06979609], true:0.0
pred:[0.0449149], true:0.0
pred:[0.05245855], true:0.0
pred:[0.7262559], true:0.0
pred:[0.6690071], true:0.0
pred:[0.6106906], true:0.0
pred:[0.9768483], true:1.0
pred:[0.6120895], true:0.0
pred:[0.49902067], true:0.0
pred:[0.39184636], true:0.0
pred:[0.32612407], true:0.0
pred:[0.26030597], true:0.0
pred:[0.2220945], true:0.0
pred:[0.19394767], true:0.0
pred:[0.17088124], true:0.0
pred:[0.], true:0.0
pred:[0.], true:0.0
pred:[0.], true:0.0
pred:[0.], true:0.0
pred:[0.], true:0.0
pred:[0.], true:0.0
pred:[0.], true:0.0
pred:[0.], true:0.0
pred:[0.], true:0.0
pred:[0.], true:0.0
pred:[0.], true:0.0
pred:[0.], true:0.0
pred:[0.], 

pred:[0.38339916], true:0.0
pred:[0.35749316], true:0.0
pred:[0.30242407], true:0.0
pred:[0.22491229], true:0.0
pred:[0.18636993], true:0.0
pred:[0.16025499], true:0.0
pred:[0.13056529], true:0.0
pred:[0.11963055], true:0.0
pred:[0.13089904], true:0.0
pred:[0.08502191], true:0.0
pred:[0.1308124], true:0.0
pred:[0.10635483], true:0.0
pred:[0.07452968], true:0.0
pred:[0.05383205], true:0.0
pred:[0.05959332], true:0.0
pred:[0.04971254], true:0.0
pred:[0.0382311], true:0.0
pred:[0.06454411], true:0.0
pred:[0.9709313], true:0.0
pred:[0.7175259], true:0.0
pred:[0.7048349], true:0.0
pred:[0.7253674], true:0.0
pred:[0.22030318], true:0.0
pred:[0.18767157], true:0.0
pred:[0.1811496], true:0.0
pred:[0.21480119], true:0.0
pred:[0.1408678], true:0.0
pred:[0.1520899], true:0.0
pred:[0.14535171], true:0.0
pred:[0.13884631], true:0.0
pred:[0.25807995], true:0.0
pred:[0.15465778], true:0.0
pred:[0.10050264], true:0.0
pred:[0.12872157], true:0.0
pred:[0.10152525], true:0.0
pred:[0.12522641], true:1.0
p

pred:[0.20811838], true:0.0
pred:[0.27228427], true:0.0
pred:[0.15284798], true:0.0
pred:[0.1281248], true:0.0
pred:[0.17814413], true:0.0
pred:[0.1346525], true:0.0
pred:[0.12237], true:0.0
pred:[0.09484416], true:0.0
pred:[0.11346295], true:0.0
pred:[0.08551729], true:0.0
pred:[0.08941543], true:0.0
pred:[0.09113592], true:0.0
pred:[0.13497421], true:0.0
pred:[0.06739077], true:0.0
pred:[0.14242917], true:0.0
pred:[0.06082103], true:0.0
pred:[0.08991027], true:0.0
pred:[0.08419991], true:0.0
pred:[0.915628], true:0.0
pred:[0.5814301], true:0.0
pred:[0.50385225], true:0.0
pred:[0.5851636], true:0.0
pred:[0.24939317], true:0.0
pred:[0.6745792], true:0.0
pred:[0.17106876], true:1.0
pred:[0.23056695], true:0.0
pred:[0.18514964], true:0.0
pred:[0.38942912], true:0.0
pred:[0.21984479], true:0.0
pred:[0.19953063], true:0.0
pred:[0.12003142], true:0.0
pred:[0.10442078], true:0.0
pred:[0.14733547], true:0.0
pred:[0.09885412], true:0.0
pred:[0.10431144], true:0.0
pred:[0.11385107], true:0.0
pr

pred:[0.28233188], true:0.0
pred:[0.45423195], true:0.0
pred:[0.32405317], true:0.0
pred:[0.24355993], true:0.0
pred:[0.30858713], true:0.0
pred:[0.2567426], true:0.0
pred:[0.14276344], true:0.0
pred:[0.47241005], true:0.0
pred:[0.10717902], true:0.0
pred:[0.10946718], true:0.0
pred:[0.08904555], true:0.0
pred:[0.19158584], true:0.0
pred:[0.09605527], true:0.0
pred:[0.09853676], true:0.0
pred:[0.07205844], true:0.0
pred:[0.06439483], true:0.0
pred:[0.0865882], true:0.0
pred:[0.06291458], true:0.0
pred:[0.20530632], true:0.0
pred:[0.6455078], true:1.0
pred:[0.41081336], true:0.0
pred:[0.1748581], true:0.0
pred:[0.12642843], true:0.0
pred:[0.13505092], true:0.0
pred:[0.30282056], true:0.0
pred:[0.9795706], true:0.0
pred:[0.55375564], true:0.0
pred:[0.4670717], true:0.0
pred:[0.5713418], true:0.0
pred:[0.392467], true:0.0
pred:[0.23872265], true:0.0
pred:[0.3415928], true:0.0
pred:[0.17067394], true:0.0
pred:[0.13912815], true:0.0
pred:[0.16162798], true:0.0
pred:[0.15125573], true:0.0
pr

pred:[0.12285766], true:0.0
pred:[0.11402082], true:0.0
pred:[0.09592536], true:0.0
pred:[0.08594903], true:0.0
pred:[0.07952622], true:0.0
pred:[0.06877729], true:0.0
pred:[0.06143954], true:0.0
pred:[0.0548386], true:0.0
pred:[0.05061597], true:0.0
pred:[0.04670244], true:0.0
pred:[0.03882965], true:0.0
pred:[0.9836534], true:1.0
pred:[0.42299384], true:0.0
pred:[0.7415933], true:0.0
pred:[0.26630342], true:0.0
pred:[0.34207487], true:0.0
pred:[0.28171635], true:0.0
pred:[0.2834947], true:0.0
pred:[0.20255336], true:0.0
pred:[0.18120128], true:0.0
pred:[0.1491369], true:0.0
pred:[0.17047623], true:0.0
pred:[0.09169081], true:0.0
pred:[0.39697698], true:0.0
pred:[0.11875477], true:0.0
pred:[0.07865942], true:0.0
pred:[0.0646323], true:0.0
pred:[0.14110494], true:0.0
pred:[0.08213231], true:0.0
pred:[0.04994375], true:0.0
pred:[0.04964355], true:0.0
pred:[0.0607183], true:0.0
pred:[0.06188166], true:0.0
pred:[0.04534945], true:0.0
pred:[0.04462168], true:0.0
pred:[0.05582672], true:0.0

pred:[0.23865256], true:0.0
pred:[0.19872415], true:0.0
pred:[0.29729584], true:0.0
pred:[0.1740857], true:0.0
pred:[0.14673886], true:0.0
pred:[0.48721272], true:0.0
pred:[0.4584603], true:0.0
pred:[0.1454792], true:0.0
pred:[0.13053888], true:0.0
pred:[0.12913468], true:0.0
pred:[0.07850304], true:0.0
pred:[0.13134691], true:0.0
pred:[0.30777788], true:0.0
pred:[0.09875005], true:0.0
pred:[0.3498196], true:1.0
pred:[0.07412335], true:0.0
pred:[0.24357557], true:0.0
pred:[0.08401123], true:0.0
pred:[0.06924281], true:0.0
pred:[0.04548618], true:0.0
pred:[0.9371275], true:1.0
pred:[0.43607765], true:0.0
pred:[0.5442535], true:0.0
pred:[0.23489508], true:0.0
pred:[0.28917387], true:0.0
pred:[0.21771637], true:0.0
pred:[0.33599788], true:0.0
pred:[0.56773], true:0.0
pred:[0.23041046], true:0.0
pred:[0.17733032], true:0.0
pred:[0.16434675], true:0.0
pred:[0.56465185], true:0.0
pred:[0.11626834], true:0.0
pred:[0.11872473], true:0.0
pred:[0.09365243], true:0.0
pred:[0.119908], true:0.0
pre

pred:[0.51546013], true:1.0
pred:[0.9663288], true:0.0
pred:[0.52791995], true:0.0
pred:[0.47706386], true:0.0
pred:[0.45103043], true:0.0
pred:[0.3793402], true:0.0
pred:[0.2266089], true:0.0
pred:[0.28423208], true:0.0
pred:[0.20758072], true:0.0
pred:[0.19576731], true:0.0
pred:[0.13203382], true:0.0
pred:[0.19264841], true:0.0
pred:[0.975297], true:0.0
pred:[0.600486], true:0.0
pred:[0.70699453], true:0.0
pred:[0.59164876], true:0.0
pred:[0.32402325], true:0.0
pred:[0.3748828], true:0.0
pred:[0.1833359], true:0.0
pred:[0.15415505], true:0.0
pred:[0.43863255], true:0.0
pred:[0.25089672], true:0.0
pred:[0.14260167], true:0.0
pred:[0.13619974], true:0.0
pred:[0.13007554], true:0.0
pred:[0.14655927], true:0.0
pred:[0.18705896], true:0.0
pred:[0.13940972], true:1.0
pred:[0.07392931], true:0.0
pred:[0.10163763], true:0.0
pred:[0.0746997], true:0.0
pred:[0.08435309], true:0.0
pred:[0.08908907], true:0.0
pred:[0.08522695], true:0.0
pred:[0.04911622], true:0.0
pred:[0.05758229], true:0.0
pr

pred:[0.16631207], true:0.0
pred:[0.1225563], true:0.0
pred:[0.16011876], true:0.0
pred:[0.11249137], true:0.0
pred:[0.16325235], true:0.0
pred:[0.07932153], true:0.0
pred:[0.10545897], true:0.0
pred:[0.10988703], true:1.0
pred:[0.08191183], true:0.0
pred:[0.15086031], true:0.0
pred:[0.2959153], true:0.0
pred:[0.06473461], true:0.0
pred:[0.20967683], true:0.0
pred:[0.98553276], true:0.0
pred:[0.7019192], true:0.0
pred:[0.3069422], true:0.0
pred:[0.30126327], true:0.0
pred:[0.21933648], true:1.0
pred:[0.4564659], true:0.0
pred:[0.16404128], true:0.0
pred:[0.16796324], true:0.0
pred:[0.18415633], true:0.0
pred:[0.11242136], true:0.0
pred:[0.3932974], true:0.0
pred:[0.15603334], true:0.0
pred:[0.09510353], true:0.0
pred:[0.09850758], true:0.0
pred:[0.11343348], true:0.0
pred:[0.1793249], true:0.0
pred:[0.08850172], true:0.0
pred:[0.10377708], true:0.0
pred:[0.07328856], true:0.0
pred:[0.04583329], true:0.0
pred:[0.06256372], true:0.0
pred:[0.06597799], true:0.0
pred:[0.12497684], true:0.0

pred:[0.23933074], true:0.0
pred:[0.34374577], true:0.0
pred:[0.26243103], true:0.0
pred:[0.2104854], true:0.0
pred:[0.14701647], true:0.0
pred:[0.21249178], true:0.0
pred:[0.13549408], true:0.0
pred:[0.16641858], true:0.0
pred:[0.11563495], true:0.0
pred:[0.16984501], true:0.0
pred:[0.09894764], true:0.0
pred:[0.08081222], true:0.0
pred:[0.10282779], true:0.0
pred:[0.06322995], true:0.0
pred:[0.17337427], true:0.0
pred:[0.05677015], true:0.0
pred:[0.04466918], true:0.0
pred:[0.11508837], true:0.0
pred:[0.16201377], true:0.0
pred:[0.07437828], true:0.0
pred:[0.04048967], true:0.0
pred:[0.9330685], true:0.0
pred:[0.7211687], true:0.0
pred:[0.5541007], true:0.0
pred:[0.50733364], true:0.0
pred:[0.64489913], true:1.0
pred:[0.55370814], true:0.0
pred:[0.33250004], true:0.0
pred:[0.24336013], true:0.0
pred:[0.3616388], true:0.0
pred:[0.25939453], true:0.0
pred:[0.60560304], true:0.0
pred:[0.], true:0.0
pred:[0.], true:0.0
pred:[0.], true:0.0
pred:[0.], true:0.0
pred:[0.], true:0.0
pred:[0.]